In [0]:
import pandas as pd
import numpy as np
import datetime
import urllib.parse
from ftplib import FTP
from io import StringIO
from sqlalchemy import create_engine
import psycopg2
conn = None
cur = None

<h2>Create Engine For PostgreSQL Database</h2>

In [0]:
server = "27.110.235.92" #"10.64.2.33"
database = "like_apps_ds_dwh"
user = "gbads"
pw_parse = urllib.parse.quote_plus("TdCxdsPh@2023")
pw = "TdCxdsPh@2023"
pd.options.display.float_format = '{:20.0f}'.format


In [0]:
engine = create_engine('postgresql+psycopg2://' + user + ':' + pw_parse + '@' + server + '/' + database)

<h2>Roster</h2>

In [0]:
# Connect to PostgreSQL Database
try:
    sql = '''
    select * from like_apps_ds_dwh.tbl_like_pso_roster_trx
    where fld_insert_date = (
	SELECT to_char(MAX(TO_TIMESTAMP(fld_insert_date, 'YYYY-MM-DD HH24:MI:SS')),'YYYY-MM-DD HH12:MI:SS') FROM like_apps_ds_dwh.tbl_like_pso_roster_trx)
    '''
    
    df_roster = pd.read_sql(sql,engine)
except Exception as error:
    print(error)

#df_roster = pd.read_csv(path + 'Roster.csv')


<h2>Available Agents [Realtime Aux]</h2>

In [0]:
# Connect to PostgreSQL Database
try:
    sql = '''
    select * from like_apps_ds_dwh.tbl_like_pso_realtime_aux_trx
    where fld_insert_date = (
	SELECT to_char(MAX(TO_TIMESTAMP(fld_insert_date, 'YYYY-MM-DD HH24:MI:SS')),'YYYY-MM-DD HH12:MI:SS') FROM like_apps_ds_dwh.tbl_like_pso_realtime_aux_trx)
    '''
    df_aux = pd.read_sql(sql,engine)
except Exception as error:
    print(error)

In [0]:
#df_aux = pd.read_excel(path + 'Realtime Aux Report.xlsb', sheet_name='Dump')
df_aux = df_aux.loc[:, ~df_aux.columns.str.replace('\.\d+','', regex=True).duplicated(keep='first')]

In [0]:
# TRANSFORM REALTIME AUX
df_aux = df_aux.fillna(0)

In [0]:
df_aux['fld_agent_id'] = df_aux['fld_agent_id'].astype(str)
#df_aux['fld_local_end_time'] = df_aux['fld_local_end_time'].apply(lambda x: (datetime.datetime(1899,12,30) + datetime.timedelta(days=x)))

# FILTER STATUS
df_aux = df_aux[df_aux['fld_status'].str.contains('available|email_backlog')]

In [0]:
# MERGE WITH ROSTER
df_available_agents = pd.merge(df_roster[['fld_employee_id', 
                                          'fld_srtrepid', 
                                          'fld_employee_name',
                                          'fld_supervisor',
                                          'fld_next_level_supervisor']
                                        ],
                         df_aux[['fld_agent_id',
                                          'fld_local_end_time', 
                                          'fld_status']
                                        ],
                         left_on='fld_srtrepid',
                         right_on='fld_agent_id')

In [0]:
df_available_agents['fld_local_end_time'] = df_available_agents['fld_local_end_time'].replace(0, np.nan)

In [0]:
df_available_agents['fld_local_end_time'] = pd.to_datetime(df_available_agents['fld_local_end_time'])
df_available_agents = df_available_agents.sort_values(by='fld_local_end_time')
df_available_agents = df_available_agents.groupby(['fld_employee_id']).first()

<h2>Closed Cases</h2>

In [0]:
# Connect to PostgreSQL Database
try:
    sql = '''
    SELECT 
        allocation.fld_job_id,
        fld_date_assigned AS fld_insert_date,
        fld_new_owner AS fld_owner,
        DATE(fld_date_assigned) AS fld_date,
        TO_CHAR(fld_date_assigned, 'HH12:00:00 AM') AS fld_interval
    FROM like_apps_ds_dwh.tbl_like_pso_backlog_allocation_fact AS allocation
    LEFT JOIN (
        SELECT DISTINCT fld_job_id FROM like_apps_ds_dwh.tbl_like_pso_backlog_alloc_trx
        WHERE fld_insert_date = (SELECT MAX(fld_insert_date) FROM like_apps_ds_dwh.tbl_like_pso_backlog_alloc_trx)
    ) AS backlog
    ON 
    allocation.fld_job_id = backlog.fld_job_id 
    WHERE backlog.fld_job_id IS NULL
'''
    
    df_close = pd.read_sql(sql,engine)
except Exception as error:
    print(error)
    


In [0]:
df_close['fld_status'] = 'Closed'

<h2>Backlog Cases</h2>

In [0]:
# Connect to PostgreSQL Database
# EXCLUDE CASES ASSIGNED ON CURRENT DAY
try:
    sql = '''
    SELECT
        backlog.* 
    from like_apps_ds_dwh.tbl_like_pso_backlog_alloc_trx AS backlog
    LEFT JOIN (
        SELECT * 
        FROM like_apps_ds_dwh.tbl_like_pso_backlog_allocation_fact
        WHERE fld_date_assigned = (SELECT MAX(fld_date_assigned) FROM like_apps_ds_dwh.tbl_like_pso_backlog_allocation_fact)
    ) AS allocation
    ON backlog.fld_job_id = allocation.fld_job_id
    WHERE
        allocation.fld_job_id is null AND
        backlog.fld_insert_date = (
        SELECT 
            to_char(MAX(TO_TIMESTAMP(fld_insert_date, 'YYYY-MM-DD HH24:MI:SS')),'YYYY-MM-DD HH12:MI:SS') 
        FROM like_apps_ds_dwh.tbl_like_pso_backlog_alloc_trx
    )
'''
    
    df_backlog = pd.read_sql(sql,engine)
except Exception as error:
    print(error)
    
#df_backlog = pd.read_excel(path + 'backlog-alloc-report-manila.xlsb',sheet_name='Raw')
df_backlog = df_backlog.replace(np.nan, None)

In [0]:
# TRANSFORM BACKLOG CASE
df_backlog.replace(np.nan, 0)

In [0]:
df_backlog = df_backlog.fillna(0)
df_backlog_case = df_backlog
df_backlog = df_backlog[df_backlog.fld_srt_job_id !=0]
df_backlog = df_backlog.dropna(subset=['fld_srt_job_id'])
#df_backlog['fld_date_created'] = df_backlog['fld_date_created'].apply(lambda x: (datetime.datetime(1899,12,30) + datetime.timedelta(days=x)))

In [0]:
df_backlog = df_backlog.loc[:,['fld_srt_job_id', 'fld_owner_copy2','fld_last_status_change_hour','fld_trt','fld_trt_range', 'fld_job_id', 'fld_date_created', 'fld_insert_date']]

In [0]:
# SELECT COLUMNS

# CREATE CUSTOM TRT RANGE
df_backlog['fld_custom_trt_range'] = df_backlog['fld_trt_range']
df_backlog['fld_custom_trt_range'] = df_backlog['fld_custom_trt_range'].apply(lambda x: x.replace('>4000','4001'))
df_backlog['fld_custom_trt_range'] = df_backlog['fld_custom_trt_range'].apply(lambda x: x.replace('<',''))
df_backlog['fld_custom_trt_range'] = df_backlog['fld_custom_trt_range'].astype(int)

# SORT BACKLOG CASE BY TRT_RANGE & LAST_STATUS_CHANGE_HOUR
df_backlog = df_backlog.sort_values(by=['fld_custom_trt_range', 'fld_last_status_change_hour'], ascending=[False, False])

df_backlog['fld_new_owner'] = 0


<h2>Case Tracker</h2>


In [0]:
# GET CASE FROM BACKLOG
df_track = df_backlog[['fld_job_id', 'fld_insert_date', 'fld_owner_copy2']]
df_track['fld_insert_date']  = pd.to_datetime(df_track['fld_insert_date'])
df_track['fld_date'] = pd.to_datetime(df_track['fld_insert_date']).dt.date
df_track['fld_interval'] = df_track['fld_insert_date'].dt.strftime('%H:00:00 %p')
df_track['fld_status'] = np.where(df_track['fld_owner_copy2']==0,'Unassigned', 'Pending')
df_track.rename(columns={"fld_owner_copy2": "fld_owner"}, inplace=True)


In [0]:
# COUNT CASES PER AGENT
#df_case_count = df_backlog_case['fld_owner'].value_counts(ascending=True).reset_index(drop=True)
df_case_count = df_backlog_case.groupby(['fld_owner'])['fld_srt_job_id'].count().reset_index()
df_case_count = df_case_count.rename(columns={'fld_owner' : 'fld_id', 'fld_srt_job_id' : 'fld_actual_case_count'})


In [0]:
# GET AVAILABLE AGENTS
df_case_count = df_case_count[df_case_count['fld_actual_case_count'] < 4]

df_case_count['fld_new_case_count'] = df_case_count['fld_actual_case_count']

In [0]:
df_available_agents['fld_agent_id'] = df_available_agents['fld_agent_id'].astype('int64')
df_available_agents = df_available_agents.reindex(columns=['fld_agent_id', 'fld_employee_id','fld_srtrepid',
                                                    'fld_employee_name',
                                                    'fld_supervisor',
                                                    'fld_next_level_supervisor',
                                                    'fld_local_end_time',
                                                    'fld_status'])

df_case_count['fld_id'] = df_case_count['fld_id'].astype('int64')

In [0]:
# MERGE AVAILABLE AGENTS & CASE COUNT
df_available_agents = pd.merge(df_available_agents[['fld_agent_id',
                                                    'fld_employee_id',
                                                    'fld_srtrepid',
                                                    'fld_employee_name',
                                                    'fld_supervisor',
                                                    'fld_next_level_supervisor',
                                                    'fld_local_end_time',
                                                    'fld_status']
                                        ],
                         df_case_count[['fld_id',
                                          'fld_actual_case_count', 
                                          'fld_new_case_count']
                                        ],
                         left_on='fld_agent_id',
                         right_on='fld_id',
                         suffixes=('_aux', '_backlog'))

df_available_agents = df_available_agents.sort_values(by='fld_local_end_time')

In [0]:
df_available_agents = df_available_agents.sort_values(by='fld_local_end_time')

# Add columns to Backlog for new owner details
df_backlog['fld_agent_name'] = ''
df_backlog['fld_supervisor'] = ''
df_backlog['fld_next_level_supervisor'] = ''


<h2>Allocate Backlog Cases to Available Agents</h2>

In [0]:
# ITERATE TO ALL AVAILABLE CASES
assign_date = datetime.datetime.now()
for case_index, case_row in df_backlog.iterrows():
    # FILTER AGENTS WITH LESS THAN 4 CASES
    #df_new_case = df_case_count[df_case_count['fld_actual_case_count'] < 4]
    # ITEREATE TO AVAILABLE AGENTS
        
    for agent_index, agent_row in df_available_agents.iterrows():
       
        if agent_row['fld_new_case_count'] < 4:
            # ASSIGN NEW OWNER
            df_backlog.at[case_index,'fld_new_owner'] = agent_row['fld_id']
            df_backlog.at[case_index,'fld_agent_name'] = agent_row['fld_employee_name']
            df_backlog.at[case_index,'fld_supervisor'] = agent_row['fld_supervisor']
            df_backlog.at[case_index,'fld_next_level_supervisor'] = agent_row['fld_next_level_supervisor']
            df_backlog.at[case_index,'fld_date_assigned'] = assign_date

            # UPDATE TRACKER - SET STATUS TO RE-ASSIGNED
            df_track.at[case_index,'fld_status'] = 'Newly Re-Assigned'

            # UDPATE CASE COUNT
            df_available_agents.at[agent_index, 'fld_new_case_count'] += 1
            break

# FILTER OUT UNASSIGNED CASES
df_backlog = df_backlog[df_backlog['fld_new_owner'] > 0 ]



In [0]:
df_backlog = df_backlog.reset_index(drop=True)

In [0]:
# APPEND WITH CLOSE CASES
df_track_combined = pd.concat([df_track, df_close], ignore_index=True)


<H2>Load to Database</H2>

In [0]:
# Backlog Allocation Fact Table
try:
    conn = psycopg2.connect(
            host=server,
            database=database,
            user=user,
            password=pw)
    print('Connected to the PostgreSQL database')
 

    cur = conn.cursor()
    
    for df_index, df_row in df_backlog.iterrows():        
        sql = '''INSERT INTO like_apps_ds_dwh.tbl_like_pso_backlog_allocation_fact
        (
        fld_srt_job_id,
        fld_owner,
        fld_last_status_change_hour,
        fld_trt,
        fld_trt_range,
        fld_job_id,
        fld_date_created,
        fld_custom_trt_range,
        fld_new_owner,
        fld_agent_name,
        fld_supervisor,
        fld_next_level_supervisor,
        fld_date_assigned
        )
        VALUES( ''' 
        sql = sql + "'" + df_row['fld_srt_job_id'] + "', "
        sql = sql + str(df_row['fld_owner_(copy_2)']) + """, """
        sql = sql + str(df_row['fld_last_status_change_hour']) + ', ' 
        sql = sql + str(df_row['fld_trt']) + ', ' 
        sql = sql + "'" + df_row['fld_trt_range'] + "', "
        sql = sql + str(df_row['fld_job_id']) + ', ' 
        sql = sql + "'" + str(df_row['fld_date_created']) + "', " 
        sql = sql + str(df_row['fld_custom_trt_range']) + ', ' 
        sql = sql + str(df_row['fld_new_owner']) + ', '  
        sql = sql + "'" + df_row['fld_agent_name'] + "', "
        sql = sql + "'" + df_row['fld_supervisor'] + "', " 
        sql = sql + "'" + df_row['fld_next_level_supervisor'] + "', " 
        sql = sql + "'" + str(df_row['fld_date_assigned']) + "')"
        
        cur.execute(sql)
        conn.commit()

except Exception as error:
    print(error )
finally:
    if cur is not None:
        cur.close()
    if conn is not None:
        conn.close()
        
         

In [0]:
# Case Tracking Table
df_track_combined.to_sql('tbl_like_pso_case_tracking_fact',engine, schema=database, if_exists='append', index=False)


<h2>Generate Summary</h2>


In [0]:
# Connect to PostgreSQL Database
try:
    sql = '''
    SELECT 
	fld_status,
	COUNT(fld_job_id)
    FROM like_apps_ds_dwh.tbl_like_pso_case_tracking_fact
    GROUP BY fld_status

'''
    
    df_summary = pd.read_sql(sql,engine)
    df_summary = df_summary.reset_index(drop=True)
except Exception as error:
    print(error)


In [0]:
# BACKLOG ALLOCATION TRACKING
try:
    sql = '''
    SELECT 
        fld_job_id, 
        MAX(fld_owner) AS Recent_Owner,
        COUNT(fld_owner) AS Owner_count,
        MIN(fld_insert_date) AS first_allocation_date,
        MAX(fld_insert_date) AS fld_insert_date,
        MAX(fld_interval) AS recent_interval,
        MAX(fld_status) AS recent_status
    FROM(
        SELECT 
            fld_job_id,
            CAST(fld_owner AS text) AS fld_owner,
            TO_CHAR(fld_date_assigned,'HH12 PM')  AS fld_interval,
            CAST (fld_date_assigned AS Date) AS fld_insert_date,
            'Pending' AS fld_status
        FROM like_apps_ds_dwh.tbl_like_pso_backlog_allocation_fact AS back
        
        UNION 
        SELECT 
            fld_job_id,
            CAST(fld_owner AS text) AS fld_owner,
            TO_CHAR(fld_interval,'HH12 PM')  AS fld_interval,
            CAST(fld_insert_date AS Date) AS fld_insert_date,
            fld_status
        FROM like_apps_ds_dwh.tbl_like_pso_case_tracking_fact AS track
        WHERE fld_status = 'Close'
    )
    GROUP BY fld_job_id
    ORDER BY recent_status
'''
    
    df_track_summary = pd.read_sql(sql,engine)
    df_track_summary = df_track_summary.reset_index(drop=True)
except Exception as error:
    print(error)


<h2>Send Email</h2>

In [0]:
from email.mime.text import MIMEText
from email.mime.multipart import MIMEMultipart
from email.mime.application import MIMEApplication
from io import StringIO

from email.message import EmailMessage
import ssl
import smtplib

e_sender = 'karl.toledo@tdcx.com'
e_pass = 'kcwp isxg jbkr evwn'
e_receiver = 'jolene.teo@tdcx.com, ruby.lenon@tdcx.com, cheddy.pagunuran@tdcx.com, yin.long@tdcx.com, karl.toledo@tdcx.com'

In [0]:
#ITERATE TO TL
df_backlog = df_backlog.sort_values(['fld_supervisor', 'fld_agent_name'])
prev_tl = ''
email_body = ''
allocation_count = len(df_backlog) - 1

for team_index, team_row in df_backlog.iterrows():
    tl = team_row['fld_supervisor']
    
    if (tl == prev_tl or team_index == 0) and team_index < allocation_count :
        email_body += team_row['fld_agent_name'] + ' - ' + str(team_row['fld_job_id']) + '\n'
    elif (len(prev_tl) > 1) :

        # SET FINAL RECORD
        if team_index == allocation_count :
            email_body += team_row['fld_agent_name'] + ' -> ' + str(team_row['fld_job_id']) + '\n'
        
        tl_name = prev_tl.split(' ', 1)[0]
        
        # SEND EMAIL
        
        subject = 'Backlog Allocation for Team ' + tl_name + '[' + str(assign_date.strftime("%m-%d %-I%p")) +']'
                
        em = EmailMessage()
        em['From'] = e_sender
        em['To'] = e_receiver
        em['Subject'] = subject
        #em.setBodyHTML(body)
        email_body = 'Hi ' + tl_name +',\n\n' +'Please see below backlog cases assigned to new agents as of '+ str(assign_date.strftime("%B %-d %-I%p")) +':\n'+ email_body +'\n\n'
        em.set_content(email_body)
        
        context = ssl.create_default_context()
        
        with smtplib.SMTP_SSL('smtp.gmail.com', 465, context=context) as smtp:
            smtp.login(e_sender, e_pass)
            smtp.sendmail(e_sender, e_receiver, em.as_string())
            smtp.quit()
        #print (email_body)

        # RESET VARIABLES
        email_body = team_row['fld_agent_name'] + ' - ' + str(team_row['fld_job_id']) + '\n'
            
    prev_tl = tl
        

<h2>Email Report</h2>

In [0]:
# CREATE SUMMARY FOR EMAIL
#Linux Format
ts = str(assign_date.strftime("%B %-d %-I%p"))
#Windows Format
#ts = str(assign_date.strftime("%B %#d %#I%p"))
msg_body = """
    <html><body><p>Hi Team,</p> <p>Please see attached file for the Backlog Case Allocation as of """ + ts + """/p>
    <style>
    table {
    font-family: arial, sans-serif;
    border-collapse: collapse;
    width: 100%;
    }
    td, th {
    border: 1px solid #dddddd;
    text-align: left;
    padding: 8px;
    }
    </style>
"""
msg_body = msg_body + '<h3>Backlog Case Summary</h3><table><tr><th>Status</th><th>Case</th></tr>'
for summary_index, summary_row in df_summary.iterrows():    
    msg_body = msg_body + '<tr><td>'+ summary_row['fld_status'] +'</td><td>'+ str(summary_row['count']) +'</td></tr>'

msg_body = msg_body + '''</table><br><h3>Case Allocation Status</h3><table><tr>
    <th style="width:3px"></th>
    <th>Job ID</th>
    <th>Recent Owner</th>
    <th>Owner Count</th>
    <th>First Allocation Date</th>
    <th>Recent Allocation Date</th>
    <th>Interval</th>
    <th>Recent Status</th>
    </tr>'''

for track_index, track_row in df_track_summary.iterrows():
    msg_body = msg_body + '<tr><td>'+ str(track_index+1) +'</td><td>'+ str(track_row['fld_job_id']) +'</td><td>'+ str(track_row['recent_owner']) +'</td><td>'+ str(track_row['owner_count']) +'</td><td>'+ str(track_row['first_allocation_date']) +'</td><td>'+ str(track_row['fld_insert_date']) +'</td><td>'+ track_row['recent_interval'] +'</td><td>'+ track_row['recent_status'] +'</td></tr>'

msg_body = msg_body + '</table></body></html>'

#e_receiver = 'karl.toledo@tdcx.com'

msg = MIMEMultipart()
msg['Subject'] = 'Backlog Allocation Report as of ' + ts
msg['From'] = e_sender
msg['To'] = e_receiver
msg.add_header('Content-Type','text/html')
#msg.attach(MIMEText('<html><body><p>Hi Team,</p> <p>Please see attached file for the Backlog Case Allocation as of ' + ts + '</p>' + msg_body, 'html'))
msg.attach(MIMEText(msg_body, 'html'))

print(msg_body)
#Backlog Case
stream_backlog = StringIO()
df_backlog.to_csv(stream_backlog,index=False)
msg.attach(MIMEApplication(stream_backlog.getvalue(), Name='Backlog Allocation.csv'))

#Available Agents
stream_agents = StringIO()
df_backlog.to_csv(stream_agents,index=False)
msg.attach(MIMEApplication(stream_agents.getvalue(), Name='Avvailable Agents.csv'))

#Case Available
stream_case = StringIO()
df_backlog.to_csv(stream_case,index=False)
msg.attach(MIMEApplication(stream_case.getvalue(), Name='Case Available.csv'))

#Case Tracking
stream_track = StringIO()
df_track_combined.to_csv(stream_track,index=False)
msg.attach(MIMEApplication(stream_track.getvalue(), Name='Case Tracking.csv'))

context = ssl.create_default_context()

with smtplib.SMTP_SSL('smtp.gmail.com', 465, context=context) as smtp:
    smtp.login(e_sender, e_pass)
    smtp.sendmail(e_sender, e_receiver, msg.as_string())